In [1]:
import sys
import os

sys.path.append("/home/vib9/src/SL-Net/superlayer/voxel")

from train import train
import argparse
import logging
import os
import sys

import numpy as np
from tqdm import tqdm
from matplotlib import pyplot as plt

import torch
import torch.nn as nn
from torch import optim
from torch.utils.tensorboard import SummaryWriter
from torch.utils.data import DataLoader, random_split

sys.path.append("../../")
sys.path.append("../../scripts/")
import superlayer.utils

from scripts import eval_net, train_net, get_args

from superlayer.models import AESuperNet, AEnet, cvpr2018_net
from superlayer.utils import BrainD, dice_coeff, one_hot, plot_img_array, plot_side_by_side

dir_img = '/home/gid-dalcaav/projects/neuron/data/t1_mix/proc/resize256-crop_x32-slice100/train/vols/'
dir_mask = '/home/gid-dalcaav/projects/neuron/data/t1_mix/proc/resize256-crop_x32-slice100/train/asegs/'

dir_train = '/home/vib9/src/SL-Net/jupyter/partitions/train.txt'
dir_val = '/home/vib9/src/SL-Net/jupyter/partitions/val.txt'
dir_scarce = '/home/vib9/src/SL-Net/jupyter/partitions/scarce_train.txt'

dir_checkpoint_1 = 'checkpoints_1/'
dir_checkpoint_2 = 'checkpoints_2/'

logging.basicConfig(level=logging.INFO, format='%(levelname)s: %(message)s')
args = get_args()
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
logging.info(f'Using device {device}')

target_label_numbers = [0,2,3,4,10,16,17,28,31,41,42,43,49,53,63]
val_percent = 0.1
batch_size = args.batchsize
lr = args.lr
img_scale = args.scale
writer = SummaryWriter(comment=f'LR_{lr}_BS_{batch_size}_SCALE_{img_scale}')
enc_nf = [64, 64, 64, 64]
dec_nf = [64, 64, 64, 64]

INFO: Using device cuda


In [ ]:
dir_i = '/home/gid-dalcaav/projects/neuron/data/t1_mix/proc/resize256-crop_x32-slice100/train/vols/'
atlas_file = '/home/vib9/src/voxelmorph/data/atlas_norm.npz'
# Prepare the vm1 or vm2 model and send to device
nf_enc = [64, 64, 64, 64]
nf_dec = [64, 64, 64, 64, 64, 64, 64]
atlas_vol = np.load(atlas_file)['vol'][np.newaxis, ..., np.newaxis][:,:,:,100,:]
vol_size = atlas_vol.shape[1:-1]

train_file = '/home/vib9/src/SL-Net/jupyter/partitions/train.txt'
val_file = '/home/vib9/src/SL-Net/jupyter/partitions/val.txt'

model1 = cvpr2018_net(vol_size, nf_enc, nf_dec)
    
train_loss1, train_recon1, val_loss1, val_recon1 = train(model1,
                                                          gpu='0',
                                                          data_dir=dir_i,
                                                          train_file=train_file,
                                                          val_file=val_file,
                                                          atlas_file=atlas_file,
                                                          lr=1e-4,
                                                          n_iter=150000,
                                                          data_loss='mse',
                                                          model='vm2',
                                                          reg_param=0.01, 
                                                          batch_size=1)

Train Epoch: 0 | Loss: 0.009043 | Reconstruction Loss: 0.009043
Train Epoch: 1 | Loss: 0.007663 | Reconstruction Loss: 0.007663
Train Epoch: 2 | Loss: 0.009626 | Reconstruction Loss: 0.009626
Train Epoch: 3 | Loss: 0.011535 | Reconstruction Loss: 0.011535
Train Epoch: 4 | Loss: 0.009869 | Reconstruction Loss: 0.009869
Train Epoch: 5 | Loss: 0.015638 | Reconstruction Loss: 0.015638
Train Epoch: 6 | Loss: 0.007780 | Reconstruction Loss: 0.007780
Train Epoch: 7 | Loss: 0.009008 | Reconstruction Loss: 0.009008
Train Epoch: 8 | Loss: 0.008267 | Reconstruction Loss: 0.008267
Train Epoch: 9 | Loss: 0.006826 | Reconstruction Loss: 0.006826
Train Epoch: 10 | Loss: 0.007571 | Reconstruction Loss: 0.007571
Train Epoch: 11 | Loss: 0.007886 | Reconstruction Loss: 0.007886


/nfs02/users/vib9/anaconda3/envs/sln/lib/python3.6/site-packages/torch/nn/functional.py:3226: UserWarning: Default grid_sample and affine_grid behavior has changed to align_corners=False since 1.3.0. Please specify align_corners=True if the old behavior is desired. See the documentation of grid_sample for details.
  warnings.warn("Default grid_sample and affine_grid behavior has changed "


Train Epoch: 12 | Loss: 0.008797 | Reconstruction Loss: 0.008797
Train Epoch: 13 | Loss: 0.008508 | Reconstruction Loss: 0.008508
Train Epoch: 14 | Loss: 0.009787 | Reconstruction Loss: 0.009787
Train Epoch: 15 | Loss: 0.007703 | Reconstruction Loss: 0.007702
Train Epoch: 16 | Loss: 0.006471 | Reconstruction Loss: 0.006471
Train Epoch: 17 | Loss: 0.009148 | Reconstruction Loss: 0.009148
Train Epoch: 18 | Loss: 0.007324 | Reconstruction Loss: 0.007324
Train Epoch: 19 | Loss: 0.006507 | Reconstruction Loss: 0.006507
Train Epoch: 20 | Loss: 0.008192 | Reconstruction Loss: 0.008192
Train Epoch: 21 | Loss: 0.008386 | Reconstruction Loss: 0.008386
Train Epoch: 22 | Loss: 0.009840 | Reconstruction Loss: 0.009840
Train Epoch: 23 | Loss: 0.007879 | Reconstruction Loss: 0.007879
Train Epoch: 24 | Loss: 0.009389 | Reconstruction Loss: 0.009389
Train Epoch: 25 | Loss: 0.009528 | Reconstruction Loss: 0.009528
Train Epoch: 26 | Loss: 0.007143 | Reconstruction Loss: 0.007143
Train Epoch: 27 | Loss: 0

Train Epoch: 138 | Loss: 0.006401 | Reconstruction Loss: 0.006383
Train Epoch: 139 | Loss: 0.008481 | Reconstruction Loss: 0.008463
Train Epoch: 140 | Loss: 0.006767 | Reconstruction Loss: 0.006754
Train Epoch: 141 | Loss: 0.005910 | Reconstruction Loss: 0.005897
Train Epoch: 142 | Loss: 0.007108 | Reconstruction Loss: 0.007096
Train Epoch: 143 | Loss: 0.008008 | Reconstruction Loss: 0.007995
Train Epoch: 144 | Loss: 0.007004 | Reconstruction Loss: 0.006991
Train Epoch: 145 | Loss: 0.006000 | Reconstruction Loss: 0.005989
Train Epoch: 146 | Loss: 0.007327 | Reconstruction Loss: 0.007315
Train Epoch: 147 | Loss: 0.009135 | Reconstruction Loss: 0.009121
Train Epoch: 148 | Loss: 0.007871 | Reconstruction Loss: 0.007854
Train Epoch: 149 | Loss: 0.010663 | Reconstruction Loss: 0.010643
Train Epoch: 150 | Loss: 0.006965 | Reconstruction Loss: 0.006943
Train Epoch: 151 | Loss: 0.010062 | Reconstruction Loss: 0.010036
Train Epoch: 152 | Loss: 0.009740 | Reconstruction Loss: 0.009704
Train Epoc

Train Epoch: 263 | Loss: 0.005617 | Reconstruction Loss: 0.005405
Train Epoch: 264 | Loss: 0.006536 | Reconstruction Loss: 0.006202
Train Epoch: 265 | Loss: 0.004815 | Reconstruction Loss: 0.004480
Train Epoch: 266 | Loss: 0.005513 | Reconstruction Loss: 0.005252
Train Epoch: 267 | Loss: 0.004938 | Reconstruction Loss: 0.004770
Train Epoch: 268 | Loss: 0.005412 | Reconstruction Loss: 0.005160
Train Epoch: 269 | Loss: 0.006125 | Reconstruction Loss: 0.005841
Train Epoch: 270 | Loss: 0.005458 | Reconstruction Loss: 0.005304
Train Epoch: 271 | Loss: 0.007002 | Reconstruction Loss: 0.006823
Train Epoch: 272 | Loss: 0.007081 | Reconstruction Loss: 0.006809
Train Epoch: 273 | Loss: 0.007474 | Reconstruction Loss: 0.007160
Train Epoch: 274 | Loss: 0.006946 | Reconstruction Loss: 0.006615
Train Epoch: 275 | Loss: 0.006079 | Reconstruction Loss: 0.005842
Train Epoch: 276 | Loss: 0.005791 | Reconstruction Loss: 0.005588
Train Epoch: 277 | Loss: 0.005766 | Reconstruction Loss: 0.005490
Train Epoc

...

Val Epoch: 401 | Loss: 0.001827 | Reconstruction Loss: 0.001145
Val Epoch: 402 | Loss: 0.001921 | Reconstruction Loss: 0.001186
Val Epoch: 403 | Loss: 0.001897 | Reconstruction Loss: 0.001271
Val Epoch: 404 | Loss: 0.001993 | Reconstruction Loss: 0.001296
Val Epoch: 405 | Loss: 0.001970 | Reconstruction Loss: 0.001220
Val Epoch: 406 | Loss: 0.001718 | Reconstruction Loss: 0.001117
Val Epoch: 407 | Loss: 0.002244 | Reconstruction Loss: 0.001563
Val Epoch: 408 | Loss: 0.005418 | Reconstruction Loss: 0.004151
Val Epoch: 409 | Loss: 0.002045 | Reconstruction Loss: 0.001296
Val Epoch: 410 | Loss: 0.003298 | Reconstruction Loss: 0.002606
Val Epoch: 411 | Loss: 0.001848 | Reconstruction Loss: 0.001156
Val Epoch: 412 | Loss: 0.002680 | Reconstruction Loss: 0.001864
Val Epoch: 413 | Loss: 0.002346 | Reconstruction Loss: 0.001636
Val Epoch: 414 | Loss: 0.001846 | Reconstruction Loss: 0.001260
Val Epoch: 415 | Loss: 0.002063 | Reconstruction Loss: 0.001384
Val Epoch: 416 | Loss: 0.002162 | Recons

Val Epoch: 530 | Loss: 0.002178 | Reconstruction Loss: 0.001398
Val Epoch: 531 | Loss: 0.001517 | Reconstruction Loss: 0.000941
Val Epoch: 532 | Loss: 0.002270 | Reconstruction Loss: 0.001620
Val Epoch: 533 | Loss: 0.002265 | Reconstruction Loss: 0.001635
Val Epoch: 534 | Loss: 0.002069 | Reconstruction Loss: 0.001366
Val Epoch: 535 | Loss: 0.001960 | Reconstruction Loss: 0.001323
Val Epoch: 536 | Loss: 0.001928 | Reconstruction Loss: 0.001299
Val Epoch: 537 | Loss: 0.002164 | Reconstruction Loss: 0.001513
Val Epoch: 538 | Loss: 0.001730 | Reconstruction Loss: 0.001098
Val Epoch: 539 | Loss: 0.001998 | Reconstruction Loss: 0.001277
Val Epoch: 540 | Loss: 0.001839 | Reconstruction Loss: 0.001165
Val Epoch: 541 | Loss: 0.002260 | Reconstruction Loss: 0.001597
Val Epoch: 542 | Loss: 0.002061 | Reconstruction Loss: 0.001376
Val Epoch: 543 | Loss: 0.002366 | Reconstruction Loss: 0.001665
Val Epoch: 544 | Loss: 0.001524 | Reconstruction Loss: 0.000940
Val Epoch: 545 | Loss: 0.002115 | Recons

Val Epoch: 659 | Loss: 0.001603 | Reconstruction Loss: 0.001013
Val Epoch: 660 | Loss: 0.001972 | Reconstruction Loss: 0.001236
Val Epoch: 661 | Loss: 0.001942 | Reconstruction Loss: 0.001185
Val Epoch: 662 | Loss: 0.002083 | Reconstruction Loss: 0.001441
Val Epoch: 663 | Loss: 0.002028 | Reconstruction Loss: 0.001333
Val Epoch: 664 | Loss: 0.001996 | Reconstruction Loss: 0.001320
Val Epoch: 665 | Loss: 0.002584 | Reconstruction Loss: 0.001802
Val Epoch: 666 | Loss: 0.002083 | Reconstruction Loss: 0.001406
Val Epoch: 667 | Loss: 0.003231 | Reconstruction Loss: 0.002174
Val Epoch: 668 | Loss: 0.002328 | Reconstruction Loss: 0.001581
Val Epoch: 669 | Loss: 0.001839 | Reconstruction Loss: 0.001165
Val Epoch: 670 | Loss: 0.001921 | Reconstruction Loss: 0.001186
Val Epoch: 671 | Loss: 0.002071 | Reconstruction Loss: 0.001323
Val Epoch: 672 | Loss: 0.002645 | Reconstruction Loss: 0.001834
Val Epoch: 673 | Loss: 0.002283 | Reconstruction Loss: 0.001572
Val Epoch: 674 | Loss: 0.002115 | Recons

Train Epoch: 100053 | Loss: 0.002335 | Reconstruction Loss: 0.001638
Train Epoch: 100054 | Loss: 0.001722 | Reconstruction Loss: 0.001106
Train Epoch: 100055 | Loss: 0.001915 | Reconstruction Loss: 0.001203
Train Epoch: 100056 | Loss: 0.002503 | Reconstruction Loss: 0.001704
Train Epoch: 100057 | Loss: 0.001730 | Reconstruction Loss: 0.001070
Train Epoch: 100058 | Loss: 0.001867 | Reconstruction Loss: 0.001215
Train Epoch: 100059 | Loss: 0.002127 | Reconstruction Loss: 0.001418
Train Epoch: 100060 | Loss: 0.002271 | Reconstruction Loss: 0.001624
Train Epoch: 100061 | Loss: 0.001861 | Reconstruction Loss: 0.001075
Train Epoch: 100062 | Loss: 0.002063 | Reconstruction Loss: 0.001372
Train Epoch: 100063 | Loss: 0.002025 | Reconstruction Loss: 0.001427
Train Epoch: 100064 | Loss: 0.001739 | Reconstruction Loss: 0.001100
Train Epoch: 100065 | Loss: 0.001681 | Reconstruction Loss: 0.001041
Train Epoch: 100066 | Loss: 0.001684 | Reconstruction Loss: 0.000989
Train Epoch: 100067 | Loss: 0.0027

Train Epoch: 100172 | Loss: 0.001966 | Reconstruction Loss: 0.001303
Train Epoch: 100173 | Loss: 0.002273 | Reconstruction Loss: 0.001557
Train Epoch: 100174 | Loss: 0.002254 | Reconstruction Loss: 0.001529
Train Epoch: 100175 | Loss: 0.001722 | Reconstruction Loss: 0.001048
Train Epoch: 100176 | Loss: 0.001710 | Reconstruction Loss: 0.001104
Train Epoch: 100177 | Loss: 0.002004 | Reconstruction Loss: 0.001200
Train Epoch: 100178 | Loss: 0.001775 | Reconstruction Loss: 0.001132
Train Epoch: 100179 | Loss: 0.003616 | Reconstruction Loss: 0.002570
Train Epoch: 100180 | Loss: 0.001900 | Reconstruction Loss: 0.001242
Train Epoch: 100181 | Loss: 0.001704 | Reconstruction Loss: 0.001070
Train Epoch: 100182 | Loss: 0.002740 | Reconstruction Loss: 0.001964
Train Epoch: 100183 | Loss: 0.002017 | Reconstruction Loss: 0.001223
Train Epoch: 100184 | Loss: 0.001929 | Reconstruction Loss: 0.001269
Train Epoch: 100185 | Loss: 0.001760 | Reconstruction Loss: 0.001061
Train Epoch: 100186 | Loss: 0.0016

In [ ]:
dir_i = '/home/gid-dalcaav/projects/neuron/data/t1_mix/proc/resize256-crop_x32-slice100/train/vols/'
atlas_file = '/home/vib9/src/voxelmorph/data/atlas_norm.npz'
# Prepare the vm1 or vm2 model and send to device
nf_enc = [64, 64, 64, 64]
nf_dec = [64, 64, 64, 64, 64, 64, 32]
atlas_vol = np.load(atlas_file)['vol'][np.newaxis, ..., np.newaxis][:,:,:,100,:]
vol_size = atlas_vol.shape[1:-1]

train_file = '/home/vib9/src/SL-Net/jupyter/partitions/train.txt'
val_file = '/home/vib9/src/SL-Net/jupyter/partitions/val.txt'

model4 = cvpr2018_net(vol_size, nf_enc, nf_dec, superblock_size=64)

train_loss4, train_recon4, val_loss4, val_recon4 = train(model4,
                                                          gpu='0',
                                                          data_dir=dir_i,
                                                          train_file=train_file,
                                                          val_file=val_file,
                                                          atlas_file=atlas_file,
                                                          lr=1e-4,
                                                          n_iter=150000,
                                                          data_loss='mse',
                                                          model='vm2',
                                                          reg_param=0.01, 
                                                          batch_size=1)

In [ ]:
domain = len(train_loss1)
x_values = [i+1 for i in range(domain)]

a1 = plt.subplot(1,2,1)
#a1.set_ylim([0, 0.005])
plt.title("Vanilla Voxelmorph")
plt.xlabel("Mini-epochs")
plt.ylabel("Loss Val")

plt.plot(x_values, train_loss1, color="blue", label="train loss")
plt.plot(x_values, train_recon1, color="orange", label="train recon")
plt.plot(x_values, train_loss1, color="red", label="val loss")
plt.plot(x_values, train_recon1, color="green", label="val recon")

plt.legend()
plt.grid()

a4 = plt.subplot(1,2,2)
#a4.set_ylim([0, 0.005])
plt.title("SLN Voxelmorph")
plt.xlabel("Mini-epochs")
plt.ylabel("Loss Val")

plt.plot(x_values, train_loss4, color="blue", label="train loss")
plt.plot(x_values, train_recon4, color="orange", label="train recon")
plt.plot(x_values, val_loss4, color="red", label="val loss")
plt.plot(x_values, val_recon4, color="green", label="val recon")

plt.legend()
plt.grid()

plt.subplots_adjust(wspace=1)

plt.show()

In [ ]:
net5 = SuperNet(input_ch=1, out_ch=15, use_bn=True, superblock_size=64, depth=4)

logging.info(f'Network:\n'
             f'\t{1} input channels\n'
             f'\t{15} output channels (classes)\n')

net5.to(device=device)
train_net(net=net5,
            epochs=8,
            batch_size=args.batchsize,
            lr=args.lr,
            device=device,
            img_scale=args.scale,
            val_percent=args.val / 100,
            checkpoint=2,
            target_label_numbers=target_label_numbers,
            writer=writer,
            train_path=dir_train,
            val_path=dir_val)

np.save("/home/vib9/src/SL-Net/superlayer/models/superblocks/SLN_64.npy",net5.W.cpu().data)

In [ ]:
net6 = AESuperNet(input_ch=1, out_ch=15, use_bn=True, superblock_size=64, depth=4)

logging.info(f'Network:\n'
             f'\t{1} input channels\n'
             f'\t{15} output channels (classes)\n')

net6.to(device=device)
train_net(net=net6,
            epochs=8,
            batch_size=args.batchsize,
            lr=args.lr,
            device=device,
            img_scale=args.scale,
            val_percent=args.val / 100,
            checkpoint=2,
            target_label_numbers=target_label_numbers,
            writer=writer,
            train_path=dir_train,
            val_path=dir_val)

np.save("/home/vib9/src/SL-Net/superlayer/models/superblocks/AE_64.npy",net6.W.cpu().data)

In [ ]:
dir_i = '/home/gid-dalcaav/projects/neuron/data/t1_mix/proc/resize256-crop_x32-slice100/train/vols/'
atlas_file = '/home/vib9/src/voxelmorph/data/atlas_norm.npz'
# Prepare the vm1 or vm2 model and send to device
nf_enc = [64, 64, 64, 64]
nf_dec = [64, 64, 64, 64, 64, 64, 32]
atlas_vol = np.load(atlas_file)['vol'][np.newaxis, ..., np.newaxis][:,:,:,100,:]
vol_size = atlas_vol.shape[1:-1]

train_file = '/home/vib9/src/SL-Net/jupyter/partitions/scarce_train.txt'
val_file = '/home/vib9/src/SL-Net/jupyter/partitions/val.txt'

model7 = cvpr2018_net(vol_size, nf_enc, nf_dec)

train_loss7, train_recon7, val_loss7, val_recon7 = train(model7,
                                                          gpu='0',
                                                          data_dir=dir_i,
                                                          train_file=train_file,
                                                          val_file=val_file,
                                                          atlas_file=atlas_file,
                                                          lr=1e-4,
                                                          n_iter=150000,
                                                          data_loss='mse',
                                                          model='vm2',
                                                          reg_param=0.01, 
                                                          batch_size=1)

In [ ]:
dir_i = '/home/gid-dalcaav/projects/neuron/data/t1_mix/proc/resize256-crop_x32-slice100/train/vols/'
atlas_file = '/home/vib9/src/voxelmorph/data/atlas_norm.npz'
# Prepare the vm1 or vm2 model and send to device
nf_enc = [64, 64, 64, 64]
nf_dec = [64, 64, 64, 64, 64, 64, 32]
atlas_vol = np.load(atlas_file)['vol'][np.newaxis, ..., np.newaxis][:,:,:,100,:]
vol_size = atlas_vol.shape[1:-1]

train_file = '/home/vib9/src/SL-Net/jupyter/partitions/scarce_train.txt'
val_file = '/home/vib9/src/SL-Net/jupyter/partitions/val.txt'

w = np.load("/home/vib9/src/SL-Net/superlayer/models/superblocks/SLN_64.npy")

model8 = cvpr2018_net(vol_size, nf_enc, nf_dec, superblock_size=64, weight=w)

train_loss8, train_recon8, val_loss8, val_recon8 = train(model8,
                                                          gpu='0',
                                                          data_dir=dir_i,
                                                          train_file=train_file,
                                                          val_file=val_file,
                                                          atlas_file=atlas_file,
                                                          lr=1e-4,
                                                          n_iter=150000,
                                                          data_loss='mse',
                                                          model='vm2',
                                                          reg_param=0.01, 
                                                          batch_size=1)

In [ ]:
dir_i = '/home/gid-dalcaav/projects/neuron/data/t1_mix/proc/resize256-crop_x32-slice100/train/vols/'
atlas_file = '/home/vib9/src/voxelmorph/data/atlas_norm.npz'
# Prepare the vm1 or vm2 model and send to device
nf_enc = [64, 64, 64, 64]
nf_dec = [64, 64, 64, 64, 64, 64, 32]
atlas_vol = np.load(atlas_file)['vol'][np.newaxis, ..., np.newaxis][:,:,:,100,:]
vol_size = atlas_vol.shape[1:-1]

train_file = '/home/vib9/src/SL-Net/jupyter/partitions/scarce_train.txt'
val_file = '/home/vib9/src/SL-Net/jupyter/partitions/val.txt'

w = np.load("/home/vib9/src/SL-Net/superlayer/models/superblocks/AE_64.npy")[:32,:,:,:]

model9 = cvpr2018_net(vol_size, nf_enc, nf_dec, superblock_size=64, weight=w)

train_loss9, train_recon9, val_loss9, val_recon9 = train(model9,
                                                          gpu='0',
                                                          data_dir=dir_i,
                                                          train_file=train_file,
                                                          val_file=val_file,
                                                          atlas_file=atlas_file,
                                                          lr=1e-4,
                                                          n_iter=150000,
                                                          data_loss='mse',
                                                          model='vm2',
                                                          reg_param=0.01, 
                                                          batch_size=1)

In [ ]:
domain2 = len(train_scores2)
x_values2 = [i+1 for i in range(domain2)]

a1 = plt.subplot(1,3,1)
#a1.set_ylim([0, 0.005])
plt.title("Vanilla Voxelmorph")
plt.xlabel("Mini-epochs")
plt.ylabel("Loss Val")

plt.plot(x_values2, train_loss7, color="blue", label="train loss")
plt.plot(x_values2, train_recon7, color="orange", label="train recon")
plt.plot(x_values2, train_loss7, color="red", label="val loss")
plt.plot(x_values2, train_recon7, color="green", label="val recon")

plt.legend()
plt.grid()

a4 = plt.subplot(1,3,2)
#a4.set_ylim([0, 0.005])
plt.title("SLN Voxelmorph")
plt.xlabel("Mini-epochs")
plt.ylabel("Loss Val")

plt.plot(x_values2, train_loss8, color="blue", label="train loss")
plt.plot(x_values2, train_recon8, color="orange", label="train recon")
plt.plot(x_values2, val_loss8, color="red", label="val loss")
plt.plot(x_values2, val_recon8, color="green", label="val recon")

plt.legend()
plt.grid()

a5 = plt.subplot(1,3,2)
#a5.set_ylim([0, 0.005])
plt.title("AE Voxelmorph")
plt.xlabel("Mini-epochs")
plt.ylabel("Loss Val")

plt.plot(x_values2, train_loss9, color="blue", label="train loss")
plt.plot(x_values2, train_recon9, color="orange", label="train recon")
plt.plot(x_values2, val_loss9, color="red", label="val loss")
plt.plot(x_values2, val_recon9, color="green", label="val recon")

plt.legend()
plt.grid()

plt.subplots_adjust(wspace=1)

plt.show()